In [1]:
from kaggle.api.kaggle_api_extended import KaggleApi
import pandas as pd
import os

# 初始化 Kaggle API
api = KaggleApi()
api.authenticate()

# 设置下载路径
download_dir = "./data"
os.makedirs(download_dir, exist_ok=True)

# 下载数据集
api.dataset_download_files(
    "vivek468/superstore-dataset-final",
    path="./data",
    unzip=True
)

csv_file = "Sample - Superstore.csv"
csv_path = os.path.join(download_dir,csv_file)

# 读取数据集
df = pd.read_csv(csv_path,encoding='ISO-8859-1')

OSError: Could not find kaggle.json. Make sure it's located in /root/.config/kaggle. Or use the environment method. See setup instructions at https://github.com/Kaggle/kaggle-api/

In [ ]:
df.head()

In [ ]:
def explore_data(df):
    print("数据基本信息如下：")
    print("字段名称:\n", df.columns.tolist())
    print("\n数据类型:\n", df.dtypes)

    print("\n数据样本如下：")
    display(df.head(3))
    print("\n数据维度:", df.shape)

    print("\n缺失值分析如下：")
    missing = df.isnull().sum()
    print("缺失值数量:\n", missing[missing > 0])
    print("\n缺失值百分比:\n", round(df.isnull().mean()[missing > 0] * 100, 2))

explore_data(df)

In [ ]:
# 统计完全重复的行数
duplicate_rows = df[df.duplicated(keep=False)]
print(f"完全重复的行数: {len(duplicate_rows)}")

In [ ]:
df['Order Date'] = pd.to_datetime(df['Order Date'], infer_datetime_format=True, errors='coerce')
df['Ship Date'] = pd.to_datetime(df['Ship Date'], infer_datetime_format=True, errors='coerce')

# 检查转换后的数据类型
print("字段类型:\n", df[['Order Date', 'Ship Date']].dtypes)

In [ ]:
stats = {
    'Sales': {
        '均值': df['Sales'].mean(),
        '中位数': df['Sales'].median(),
        '标准差': df['Sales'].std(),
        '峰度': df['Sales'].kurtosis(),
        '偏度': df['Sales'].skew()
    },
    'Profit': {
        '均值': df['Profit'].mean(),
        '中位数': df['Profit'].median(),
        '标准差': df['Profit'].std(),
        '峰度': df['Profit'].kurtosis(),
        '偏度': df['Profit'].skew()
    }
}
print(stats)

In [ ]:
# 按产品和地区分组分析
grouped = df.groupby(["Category","Region"]).agg({
    "Sales":["sum","mean","median"],
    "Profit":["sum","mean","median",lambda x:(x<0).mean()]
}).round(2)

# 重新命名列名
grouped.columns = ["销售额总和","平均销售额","销售额中位数",
                   "利润总和","平均利润","利润中位数","亏损比例"]

# 输出结果
print("按产品和地区分组的销售表现如下：")
print(grouped.sort_values(by="利润总和",ascending=False))

# 计算利润率
grouped["利润率"] = (grouped["利润总和"]/grouped["销售额总和"]).round(3)
print("\n利润率排名为：")
print(grouped["利润率"].sort_values(ascending=False))

In [ ]:
# 按年趋势分析
yearly_trend = df.groupby(df['Order Date'].dt.year).agg({
    "Sales":'sum',
    "Profit":'sum',
    "Order ID":'count'
}).rename(columns={"Order ID":"Order Count"})

# 计算年平均利润率
yearly_trend["Profit Margin"] = yearly_trend["Profit"] / yearly_trend["Sales"]

# 按月趋势分析
monthly_trend = df.groupby([
    df['Order Date'].dt.year.rename("Year"),
    df["Order Date"].dt.month.rename("Month")
]).agg({
    'Sales':"sum",
    "Profit":'sum',
}).reset_index()

# 创建年月标签
monthly_trend['Year-Month'] = monthly_trend['Year'].astype(str) + '-' + monthly_trend['Month'].astype(str).str.zfill(2)

# 输出结果
print("年度趋势如下：")
print(yearly_trend[["Sales","Profit","Profit Margin"]].round(2))
print("\n月度趋势如下：")
print(monthly_trend.tail(12).set_index("Year-Month")[["Sales","Profit"]].round(2))

In [ ]:
# 按产品聚合统计利润
product_profit = df.groupby("Product Name").agg({
    "Profit":['sum','mean','count'],
    "Sales":"sum"
}).sort_values(('Profit','sum'),ascending=False)

product_profit.columns = ['Total Profit', 'Avg Profit', 'Order Count', 'Total Sales']

# 选择利润前十的产品
top_products = product_profit.head(10).round(2)
print("利润最高的前十个产品有：")
print(top_products)

In [ ]:
import matplotlib.pyplot as plt

plt.figure(figsize=(14, 8))

# --- 年度趋势 ---
plt.subplot(2, 1, 1)
# 销售额柱状图
plt.bar(yearly_trend.index,yearly_trend['Sales'],
        width=0.6, alpha=0.7, label='Sales')
# 利润折线图（右轴）
plt.twinx()
plt.plot(yearly_trend.index, yearly_trend['Profit'],
         'r-o', linewidth=2, markersize=8, label='Profit')
plt.title('Annual Sales & Profit Trend')
plt.grid(ls=':')
plt.legend()

# --- 月度趋势 ---
plt.subplot(2, 1, 2)
# 销售额柱状图
plt.bar(monthly_trend['Year-Month'], monthly_trend['Sales'],
        width=0.8, alpha=0.7, label='Sales')
# 利润折线图（右轴）
plt.twinx()
plt.plot(monthly_trend['Year-Month'], monthly_trend['Profit'],
         'r-o', linewidth=2, markersize=5, label='Profit')

# 优化横轴
ax = plt.gca()  # 获取当前轴对象
ax.set_xticks(monthly_trend['Year-Month'][::3])  # 每3个月显示一个刻度

plt.title('Monthly Sales & Profit Trend')
plt.xticks(rotation=45, ha='right')
plt.grid(ls=':')
plt.legend()

plt.tight_layout()
plt.show()

In [ ]:
import matplotlib.pyplot as plt

# 准备数据
category_sales = df.groupby('Category')['Sales'].sum().sort_values(ascending=False)

# 创建图形
plt.figure(figsize=(10, 8))

# 设置颜色
colors = ['#1F77B4', '#5D9BFF', '#A5C8FF']
explode = (0.2, 0, 0)

# 绘制饼图
plt.pie(category_sales,
        labels=category_sales.index,
        autopct='%1.1f%%',
        startangle=90,
        colors=colors,
        explode=explode,
        textprops={'fontsize': 12})

plt.title('Sales Distribution by Product Category', pad=20)

plt.legend(title="Categories",
           loc="center left",
           bbox_to_anchor=(1, 0.5))

plt.tight_layout()
plt.show()

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

# 按地区聚合数据
region_data = df.groupby('Region').agg({
    'Sales': 'sum',
    'Profit': 'sum'
}).sort_values('Sales', ascending=False)

plt.figure(figsize=(12, 6))

# 设置位置和宽度
x = np.arange(len(region_data.index))
width = 0.35

# 销售额柱状图（蓝色）
plt.bar(x - width/2, region_data['Sales'], width,
        label='Sales', color='#1F77B4', alpha=0.7)

# 利润柱状图（红色）
plt.bar(x + width/2, region_data['Profit'], width,
        label='Profit', color='#FF7F0E', alpha=0.7)

plt.xticks(x, region_data.index)
plt.title('Sales & Profit by Region', pad=20)
plt.xlabel('Region')
plt.ylabel('Amount')
plt.grid(axis='y', ls=':')
plt.legend()

for i in x:
    plt.text(i - width/2, region_data['Sales'][i] + 1000,
             f"{region_data['Sales'][i]/1000:.1f}K",
             ha='center', fontsize=9)
    plt.text(i + width/2, region_data['Profit'][i] + 1000,
             f"{region_data['Profit'][i]/1000:.1f}K",
             ha='center', fontsize=9)

plt.tight_layout()
plt.show()

In [ ]:
# 设置图形样式
plt.figure(figsize=(12, 8))
plt.style.use('seaborn-v0_8')

# 绘制散点图
scatter = plt.scatter(
    x=df['Sales'],
    y=df['Profit'],
    c=df['Quantity'],
    cmap='viridis',
    alpha=0.7,
    s=50
)

z = np.polyfit(df['Sales'], df['Profit'], 1)
p = np.poly1d(z)
plt.plot(df['Sales'], p(df['Sales']), "r--", linewidth=2)

plt.title('Sales vs Profit Correlation', fontsize=16, pad=20)
plt.xlabel('Sales Amount', fontsize=12)
plt.ylabel('Profit', fontsize=12)

cbar = plt.colorbar(scatter)
cbar.set_label('Quantity Sold', rotation=270, labelpad=15)

plt.grid(True, linestyle='--', alpha=0.6)
plt.xlim(left=0)
plt.ylim(bottom=min(df['Profit'])*1.1, top=max(df['Profit'])*1.1)

plt.tight_layout()
plt.show()

In [ ]:
# --- 1. 按子类别划分的销售额和利润 ---
# 按子类别分组数据并计算销售额和利润的总和
subcategory_performance = df.groupby('Sub-Category').agg(
    Sales=('Sales', 'sum'),
    Profit=('Profit', 'sum')
).sort_values(by='Sales', ascending=False)

plt.figure(figsize=(14, 10))

# 创建按子类别划分的销售额柱状图
plt.subplot(2, 1, 1) # 2 行，1 列，第一个图
sns.barplot(x=subcategory_performance.index, y=subcategory_performance['Sales'], palette='Blues_d')
plt.title('按子类别划分的总销售额', fontsize=16, pad=20)
plt.xlabel('子类别', fontsize=12)
plt.ylabel('总销售额', fontsize=12)
plt.xticks(rotation=45, ha='right')
plt.grid(axis='y', linestyle='--', alpha=0.7)

# 创建按子类别划分的利润柱状图
plt.subplot(2, 1, 2) # 2 行，1 列，第二个图
sns.barplot(x=subcategory_performance.index, y=subcategory_performance['Profit'], palette='Greens_d')
plt.title('按子类别划分的总利润', fontsize=16, pad=20)
plt.xlabel('子类别', fontsize=12)
plt.ylabel('总利润', fontsize=12)
plt.xticks(rotation=45, ha='right')
plt.grid(axis='y', linestyle='--', alpha=0.7)

plt.tight_layout()
plt.show()

# --- 2. 折扣与利润（按类别着色） ---
plt.figure(figsize=(12, 8))
sns.scatterplot(
    x='Discount',
    y='Profit',
    hue='Category', # 按类别为点着色
    size='Sales', # 按销售额大小调整点的大小以显示量级
    sizes=(20, 400), # 点的大小范围
    alpha=0.7,
    data=df,
    palette='viridis'
)

# 添加回归线
sns.regplot(x='Discount', y='Profit', data=df, scatter=False, color='red', line_kws={'linestyle':'--', 'alpha':0.7})

plt.title('折扣与利润关系（按类别划分）', fontsize=16, pad=20)
plt.xlabel('折扣', fontsize=12)
plt.ylabel('利润', fontsize=12)
plt.grid(True, linestyle='--', alpha=0.6)
plt.legend(title='类别', bbox_to_anchor=(1.05, 1), loc='upper left')
plt.tight_layout()
plt.show()